# Classifying Images with the Scattering Transform

Run first the following commands (because they might take time) and keep reading the rest of the notebook. They simply precompute some filters that will be useful later.

In [ ]:
import numpy as np
import matplotlib.image as mpimg
import matplotlib.pyplot as plt
import scipy.signal
import matplotlib as mpl
import matplotlib.cm as cm
%matplotlib inline

from kymatio import Scattering2D
N=128
J=7

scattering_ord_1 = Scattering2D(J=J, shape=(N,N), max_order=1, frontend='numpy')
scattering_ord_2 = Scattering2D(J=J, shape=(N,N), frontend='numpy')


The following function might be useful to display a complex signal.

In [ ]:
# This function colorizes a complex signal according to its phase.
def colorize(z):
    n, m = z.shape
    c = np.zeros((n, m, 3))
    c[np.isinf(z)] = (1.0, 1.0, 1.0)
    c[np.isnan(z)] = (0.5, 0.5, 0.5)

    idx = ~(np.isinf(z) + np.isnan(z))
    A = (np.angle(z[idx]) + np.pi) / (2*np.pi)
    A = (A + 0.5) % 1.0
    B = 1.0/(1.0 + abs(z[idx])**0.3)
    c[idx] = [hls_to_rgb(a, b, 0.8) for a, b in zip(A, B)]
    return c

This function will be useful to display first order coefficient scattering and we will discuss it later.

In [ ]:
def plot_scattering_disk(src_img,scattering_coefficients,J,L=8):
    fig,ax = plt.subplots()

    scattering_coefficients = -scattering_coefficients
    scattering_coefficients = scattering_coefficients[1:, :, :]
    norm = mpl.colors.Normalize(scattering_coefficients.min(), scattering_coefficients.max(), clip=True)
    mapper = cm.ScalarMappable(norm=norm, cmap="gray")
    nb_coeffs, window_rows, window_columns = scattering_coefficients.shape
    plt.imshow(1-src_img,cmap='gray',interpolation='nearest', aspect='auto')
    ax.axis('off')
    offset = 0.1
    for row in range(window_rows):
        for column in range(window_columns):
            ax=fig.add_subplot(window_rows, window_columns, 1 + column + row * window_rows, projection='polar')
            ax.set_ylim(0, 1)
            ax.axis('off')
            ax.set_yticklabels([])  # turn off radial tick labels (yticks)
            ax.set_xticklabels([])  # turn off degrees
            # ax.set_theta_zero_location('N')  # 0° to North
            coefficients = scattering_coefficients[:, row, column]
            for j in range(J):
                for l in range(L):
                    coeff = coefficients[l + (J - 1 - j) * L]
                    color = mpl.colors.to_hex(mapper.to_rgba(coeff))
                    ax.bar(x=(4.5+l) *  np.pi / L,
                           height=2*(2**(j-1) / 2**J),
                           width=2 * np.pi / L,
                           bottom=offset + (2**j / 2**J) ,
                           color=color)
                    ax.bar(x=(4.5+l+L) * np.pi / L,
                           height=2*(2**(j-1) / 2**J),
                           width=2 * np.pi / L,
                           bottom=offset + (2**j / 2**J) ,
                           color=color)

We propose to study the Scattering Transform of order at most 2, which is explicitely given by for a signal $x\in L^2(\mathbb{R}^d)$ by:
$$S^0 x =|x| \star \phi_J,$$
$$S^1[\lambda_1] x =|x\star \psi_{\lambda_1}|\star \phi_J,$$
$$S^2[\lambda_1,\lambda_2] x =||x\star \psi_{\lambda_1}|\star \psi_{\lambda_2}|\star \phi_J,$$

and $S_2x=[S^0x,S^1x,S^2x], S_1x=[S^0x,S^1x]$.

for $|\lambda_2|\geq |\lambda_1|$, where $\lambda=(2^j,\theta)$ such that we write $|\lambda|=2^j$. As during the lectures, for $\lambda=(2^j,\theta)$,
$$\psi_{\lambda}(u)=\frac{1}{2^{2j}}\psi(\frac{r_{-\theta}u}{2^j})$$
$$\phi_J(u)=\frac{1}{2^{2J}}\phi(\frac{u}{2^J})$$
We assume that $0\leq j<J$ and that $\theta \in \Theta=\{\frac{0\pi}{4},...,\frac{7\pi}{4}\}\subset[0,2\pi]$.
    

1. Assume that $\exists \eta_0:\int_{\Vert \omega\Vert<\eta_0}|\hat \kappa(\omega)|^2d\omega>\epsilon$ and assume we can write $\hat\psi(\omega)=\hat\kappa(\omega-\omega_0)$, then show that:
$$\Vert x_a\star \psi-e^{-i\omega_0^Ta}x\star\psi\Vert\leq \Vert x\Vert\sqrt{\Vert a\Vert^2\eta_0^2+4\epsilon^2}\,.$$ Show furthermore that $|x\star\psi|=|x^{\omega_0}\star\kappa|$, where $\hat x^{\omega_0}(\omega)=\hat x(\omega+\omega_0)$.

Deduce why $|\lambda_2|\geq |\lambda_1|$.

2. Explain why $\Theta \cap [\pi,2\pi]=\{\}$.

3. Show the filters used by a (2D) Scattering Transform, for $J=3$. __Hint:__ Use https://www.kymat.io/gallery_2d/plot_filters.html. Comment them using the previous questions.

4. Compute the (1D or 2D) Scattering Transform of a pure wave signal and explain the analogy of the Scattering with a Fourier Transform.  You can use the function `plot_disk_scattering`. Explain this function. __Hint:__ Fig 4. of https://arxiv.org/pdf/1203.1513.pdf can be helpful...

5. Is a (2D) Scattering Transform a diffeomorphism? Propose an example of signal $x\in\mathbb{R}^D$ which can not be the output of a Scattering Transform.

6. Verify numerically that the Scattering is stable to small translations and verify that the scale parameter of the Scattering Transform $J$ increases, then $S_J$ is more robust to small translations.

In [ ]:
texture = mpimg.imread('texture2.jpg')
texture = np.sum(texture,axis=2)

We will now study briefly the Expected Scattering which is defined for a stationary process $x(u)$ by:
$$\bar S^0 x =\mathbf{E}[|x|],$$
$$\bar S^1[\lambda_1] x =\mathbf{E}[|x\star \psi_{\lambda_1}|]$$
$$\bar S^2[\lambda_1,\lambda_2] x =\mathbf{E}[||x\star \psi_{\lambda_1}|\star \psi_{\lambda_2}|].$$

7. Show that:
$$S^0 x =\int|x| ,$$
$$S^1[\lambda_1] x =\int |x\star \psi_{\lambda_1}|,$$
$$S^2[\lambda_1,\lambda_2] x =\int ||x\star \psi_{\lambda_1}|\star \psi_{\lambda_2}|,$$ is an unbiased estimator of $\bar S$

8. Consider the following signal: construct explicitely another signal with the same power-spectrum. Demonstrate numerically that a (2D) Scattering Transform can discriminate the two. Relate the spectral density to the squared first order coefficients. __Hint:__ Use the same distance as p8 of https://arxiv.org/pdf/1203.1513.pdf.

In [ ]:
texture = mpimg.imread('texture2.jpg')
texture = texture[:2*N,:2*N]
texture = np.sum(texture,axis=2)
# let's make it gray scale
plt.imshow(texture)
mu = np.mean(texture)
texture = texture- mu

9. Can you comment on the low-pass filter for the previous experiment?

10. Reconstruct a signal from its 2D-Scattering coefficients.

11. Explain why this Scattering Transform is not able to discriminate rotations. Find an example of signals $x,x'$ that can not be discriminated by $S$. Hint: use different mother wavelets, e.g., Cauchy wavelets.

12. Classify the 100 first samples of MNIST. You can use again some code from the previous lab.